In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import sys
import os
import pingouin as pg
import scipy.stats as stats
import statsmodels.api as sm
import statsmodels.formula.api as smf
from sklearn.decomposition import PCA
from sklearn.impute import SimpleImputer
from sklearn.cluster import KMeans
from matplotlib.lines import Line2D
import matplotlib.lines as mlines
import math
import seaborn as sns
from scipy.optimize import curve_fit

/Users/jialexu/opt/anaconda3/lib/python3.7/site-packages/outdated/utils.py:18: OutdatedPackageWarning: The package outdated is out of date. Your version is 0.2.1, the latest is 0.2.2.
Set the environment variable OUTDATED_IGNORE=1 to disable these warnings.
  **kwargs


In [2]:
traitlist1 = pd.read_csv('/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/experiments/Gwas/data/phenotype/20220614/traits.txt',sep=' ')
traitlist1 = list(traitlist1.columns)[1:]
traitlist2 = pd.read_csv('/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/experiments/Gwas/data/phenotype/20220822/traits.txt',sep=' ')
traitlist2 = list(traitlist2.columns)[1:]

In [ ]:
def mlma_read(directory, trait_num):
    file_path = directory+'Trait'+str(trait_num)+'.loco.mlma'
    df_mlma = pd.read_csv(file_path,header=0, sep='\t', index_col=0)
    df_mlma.insert(0, '-log10_P', df_mlma['p'].apply(lambda x: math.log(x, 10)*(-1)))
    df_mlma = df_mlma.set_index('SNP')
    return df_mlma

In [ ]:
## read the mlma for parameters averaged across four trials
path1 = '/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/experiments/Gwas/data/MLMA/20220614/'
df_mlma_list1=[]
for i in range(1,7):
    df_mlma1=mlma_read(path1, i)
    df_mlma_list1.append(df_mlma1['-log10_P'])
df_meta_mlma1 = pd.concat(df_mlma_list1, axis=1, keys = traitlist1[:6])


In [ ]:
## read the mlma for parameters of each trial
path2 = '/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/experiments/Gwas/data/MLMA/20220822/'
df_mlma_list2=[]
for i in range(7,42):
    df_mlma2=mlma_read(path2, i)
    df_mlma_list2.append(df_mlma2['-log10_P'])
df_meta_mlma2 = pd.concat(df_mlma_list2, axis=1, keys = traitlist2[6:])

In [ ]:
## combine all mlma data into one dataset
df_meta_mlma = pd.concat((df_meta_mlma1, df_meta_mlma2),axis=1)
##reorganize the order of columns

df_meta_mlma.insert(0, 'Chr', df_meta_mlma.index.str.split(':').str[0])
df_meta_mlma.insert(1, 'Pos', df_meta_mlma.index.str.split(':').str[1])
df_meta_mlma.rename(columns = {'DZE':'DET', 'DZEAD':'DEAD', 'LTFDZE':'LTFDE'},inplace=True)
df_meta_mlma = df_meta_mlma.loc[:,~(df_meta_mlma.columns.str.contains('PCCI')|df_meta_mlma.columns.str.contains('Std'))]
newcolumns = df_meta_mlma.columns[:9]
for i in range (1,5):
    newcolumns = newcolumns.append(df_meta_mlma.columns[df_meta_mlma.columns.str.contains('T'+str(i))])
df_meta_mlma = df_meta_mlma[newcolumns]
df_meta_mlma


In [3]:
import pickle
with open('/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/experiments/Gwas/data/LD_block/20220822/ld_block_info_20220822.pkl', 'rb') as f:
    df_ld_block = pickle.load(f)
df_ld_block = df_ld_block.loc[df_ld_block['peak_snp_log10P']>6.81]
with open('/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/experiments/Gwas/data/MLMA/20220822/df_meta_mlma.pkl', 'rb') as f:
    df_meta_mlma = pickle.load(f)

In [4]:
### develop a function for making a manhattan plot of each trait 
### with the GWAS result dataset as the input variable
def manhattan_plot_all(df_association,trait_name, output_dir):
    f, ax = plt.subplots(1,25, figsize=(100,10),sharey=True)
    plt.subplots_adjust(wspace=0.1,hspace=0.5)
    ax[0].tick_params('y', length=20, width=2, which='major')
    ax[0].set_yticks(np.arange(0,12,2))
    ax[0].set_yticklabels(np.arange(0,12,2), fontsize=60)
    plt.ylim(0,13)
    plt.suptitle(trait_name,fontsize=60)
    color1_list=['#17202A', '#626567']
    for i in range (0, 25):
        chr_num=list(df_association.groupby('Chr'))[i][0]
        chr_num=int(chr_num)
        color1 = color1_list[chr_num%2]
        axc=ax[chr_num-1]
        df=list(df_association.groupby('Chr'))[i][1]
        df1=df.loc[df['-log10_P']>6.81]
        df2=df.loc[df['-log10_P']<=6.81]
        for df_plot, color, size in zip ([df1,df2], ['#FF5733',color1], [3,1]):
            if df_plot.shape[0]>0:
                df_plot.plot(kind='scatter', x='Pos', y='-log10_P', ax=axc, c=color,s=2*100*size)
        axc.set_xlabel(str(chr_num), fontsize=60,labelpad=20)
        axc.set_xticks([])
        axc.set_ylabel(r'$-log_{10}P$-value', fontsize=60, labelpad=20)
        axc.spines['top'].set_visible(False)
        axc.spines['right'].set_visible(False)
        axc.spines['left'].set_visible(False)
    plt.savefig(output_dir+trait_name+'.tiff', dpi=300, format='tiff', bbox_inches='tight',
                facecolor='auto', edgecolor='auto',backend=None)

## make manhattan plot for each trait individually
output_dir = '/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/experiments/Gwas/data/MLMA/20220822/'
for trait_name in df_meta_mlma.columns[2:]:
    df_mlma = df_meta_mlma[['Chr','Pos',trait_name]]
    df_mlma.rename(columns={trait_name:'-log10_P'},inplace=True)
    manhattan_plot_all(df_mlma, trait_name, output_dir)
    print(trait_name)

/Users/jialexu/opt/anaconda3/lib/python3.7/site-packages/pandas/core/frame.py:5047: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


KeyboardInterrupt: 

Error in callback <function flush_figures at 0x7fc22d4ced40> (for post_execute):


KeyboardInterrupt: 

In [13]:
df_ld_block['ID'] = df_ld_block.index+":"+df_ld_block['trait']
peak_snp = df_ld_block['ID']
def classify(x):
    
    if x in list(peak_snp):
        return 's'
    else:
        return 'ns'

f, ax = plt.subplots(1,25, figsize=(100,25),sharey=True)
plt.subplots_adjust(wspace=0,hspace=0.5)
plt.yticks(np.arange(0,12,2),np.arange(0,12,2))

ax[0].set_yticklabels(np.arange(0,12,2),fontsize=80)
plt.ylim(0,12)
markers = ["o","^","v","<",">"]
color1_list=['#17202A', '#626567']
#color2_list=['#DE8CBB','#B0DAEF','#BAACE8','#F9C2C9','#F8D692','#C5E0B4','#F8CBAD']
color2_list=sns.color_palette("tab10")
for num in range (0, 25):
    if num%5 == 0:
        print(num)
    chr_num=list(df_meta_mlma.groupby('Chr'))[num][0]
    chr_num=int(chr_num)
    axc=ax[chr_num-1]
    df1 = list(df_meta_mlma.groupby('Chr'))[num][1]
    color1 = '#878c8e'
    #color1 = color1_list[chr_num%2]
    for i, trait in enumerate (df1.columns[2:]):
        color2 = color2_list[i%7]
        label = trait+'_cat'
        df = df1.copy()
        if i>0 and df[trait].max()<6.81:
            next
        else:
            df.insert(0,'label_1', df.index+":"+trait)
            df.insert(0, label, df['label_1'].apply(lambda x: classify(x)))
            df['Pos']=df['Pos'].astype('int32')
            axc.scatter(x=df['Pos'], y=df[trait], c=df[label].map({'ns':color1, 's':color2}),
                            s=df[label].map({'ns':100, 's':1500}), marker=markers[i//7], edgecolor=df[label].map({'ns':'black','s':'black'}))
            xlabel=str(chr_num)
            axc.set_xlabel(xlabel, fontsize=80,labelpad=10)
            axc.axes.xaxis.set_ticks([])
            #axc.axhline(y=6.81,linestyle = '--', linewidth = 10, color='#e41a1c')
            if num == 0:
                axc.set_ylabel('')
                #axc.set_ylabel(r'$-log_{10}P$-value', fontsize=100)
                axc.tick_params(axis='y', direction='out', length=15)
            axc.spines['top'].set_visible(False)
            axc.spines['right'].set_visible(False)
            axc.spines['left'].set_visible(False)
    
#plt.savefig('/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/doc/Figures/Initial_submit/Figure_3C_1.pdf',
            #format='pdf', bbox_inches='tight')
plt.show()


0
5
10
15
20


In [14]:
import matplotlib.lines as mlines
dic = {'DET':'TDEN', 'DEAD':'ADED', 'LTFDE':'LFDE', 'DZTD':'TDDZ'}
traits_list = []
for element in df_meta_mlma.columns[2:]:
    if '_' in element and element.split('_')[1] in list(dic.keys()):
        traits_list.append(element.replace(element.split('_')[1], dic[element.split('_')[1]]))
    elif element in list(dic.keys()):
        traits_list.append(dic[element])
    else:
        traits_list.append(element)
color2_list=sns.color_palette("tab10")
#color2_list=["#e71761","#41bbc5", "#c08080", "#788c3b", "#7377ec", "#3db366", "#ca9519"]
#color2_list=['#DE8CBB','#B0DAEF','#BAACE8','#F9C2C9','#F8D692','#C5E0B4','#F8CBAD']
markers = ["o","^","v","<",">"]
traitmarkerlist = []
for i in range (0,7):
    for j in range (0,5):
        trait_num = i+j*7
        trait = traits_list[i+j*7]
        color = color2_list[trait_num%7]
        marker = markers[trait_num//7]
        trait_marker = mlines.Line2D([], [], color=color, marker=marker, linestyle='None',markersize=6, label=trait)
        traitmarkerlist.append(trait_marker)
plt.figure(figsize=(10,1))
plt.legend(handles=traitmarkerlist,framealpha=1, ncol=7, frameon=False, fontsize=20,
           handletextpad=1,borderaxespad=0,markerscale=4, handlelength=2)
plt.axis('off')
plt.savefig('/Users/jialexu/Desktop/Project2GWAS-BehvaioralGenetics/doc/Figures/Initial_submit/Figure_3C_2.tiff', 
            format='tiff', dpi=300, bbox_inches='tight')
